Gradient Boosted Regression (GBR) algorithm to determine the best yield prediction parameters. GridsearchCV and RandomizedCV harnessed.

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
from statsmodels.stats.outliers_influence import variance_inflation_factor

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [2]:
dataset = pd.read_csv('maja_6_clim.csv')
X = dataset.iloc[:, :-1].values
y = dataset.iloc[:, -1].values

In [3]:
#VIF
X=dataset.drop(["Rice_yield", "Emer_to_har", "total_length", "Temp_range", "Min_temp", "SAVI_ripe", "EVI_ripe", "NDVI_ripe", "hum", "EVI_repro", "NDVI_repro", "Max_temp", "Sun_light", "SAVI_veg", "NDVI_veg", "EVI_veg", "Total_precip_days", "Wet_day_freq"], axis=1)
vif = pd.DataFrame()
vif["features"] = X.columns
vif["vif_Factor"] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]
print(vif)

         features  vif_Factor
0  Seedling_stage    8.956572
1    Drought_days    5.018486
2      SAVI_repro   11.499816


In [4]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 42)

## RandomizedSearchCV

In [5]:
from sklearn.ensemble import GradientBoostingRegressor
regressor = GradientBoostingRegressor()
regressor.fit(X_train, y_train)

GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                          init=None, learning_rate=0.1, loss='ls', max_depth=3,
                          max_features=None, max_leaf_nodes=None,
                          min_impurity_decrease=0.0, min_impurity_split=None,
                          min_samples_leaf=1, min_samples_split=2,
                          min_weight_fraction_leaf=0.0, n_estimators=100,
                          n_iter_no_change=None, presort='deprecated',
                          random_state=None, subsample=1.0, tol=0.0001,
                          validation_fraction=0.1, verbose=0, warm_start=False)

In [6]:
from sklearn.model_selection import RandomizedSearchCV
from pprint import pprint

# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 150, stop = 10000, num = 1)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(1, 100, num = 1)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [0.5, 1, 2, 4, 8, 16, 20]
# Minimum number of samples required at each leaf node
min_samples_leaf = [0.5, 1, 2, 4, 8, 12, 16, 20, 25, 30]

learning_rate = [0.01, 0.02, 0.04, 0.08, 0.1]

# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'learning_rate': learning_rate}

pprint(random_grid)

{'learning_rate': [0.01, 0.02, 0.04, 0.08, 0.1],
 'max_depth': [1, None],
 'max_features': ['auto', 'sqrt'],
 'min_samples_leaf': [0.5, 1, 2, 4, 8, 12, 16, 20, 25, 30],
 'min_samples_split': [0.5, 1, 2, 4, 8, 16, 20],
 'n_estimators': [150]}


In [7]:
regressor = GradientBoostingRegressor(random_state=42)
regressor_random = RandomizedSearchCV(estimator=regressor, param_distributions=random_grid, n_iter=10000, cv=5, verbose=5, random_state=42, n_jobs=-1)
regressor_random.fit(X_train, y_train)

Fitting 5 folds for each of 1400 candidates, totalling 7000 fits


/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_search.py:281: UserWarning: The total space of parameters 1400 is smaller than n_iter=10000. Running 1400 iterations. For exhaustive searches, use GridSearchCV.
  % (grid_size, self.n_iter, grid_size), UserWarning)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  14 tasks      | elapsed:    1.6s
[Parallel(n_jobs=-1)]: Done 210 tasks      | elapsed:    6.4s
[Parallel(n_jobs=-1)]: Done 570 tasks      | elapsed:   15.1s
[Parallel(n_jobs=-1)]: Done 1074 tasks      | elapsed:   27.9s
[Parallel(n_jobs=-1)]: Done 1722 tasks      | elapsed:   44.1s
[Parallel(n_jobs=-1)]: Done 2514 tasks      | elapsed:  1.1min
[Parallel(n_jobs=-1)]: Done 3450 tasks      | elapsed:  1.5min
[Parallel(n_jobs=-1)]: Done 4530 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 5754 tasks      | elapsed:  2.4min
[Parallel(n_jobs=-1)]: Done 7000 out of 7000 | elapsed:  2.9min finished


RandomizedSearchCV(cv=5, error_score=nan,
                   estimator=GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0,
                                                       criterion='friedman_mse',
                                                       init=None,
                                                       learning_rate=0.1,
                                                       loss='ls', max_depth=3,
                                                       max_features=None,
                                                       max_leaf_nodes=None,
                                                       min_impurity_decrease=0.0,
                                                       min_impurity_split=None,
                                                       min_samples_leaf=1,
                                                       min_samples_split=2,
                                                       min_weight_fraction_leaf=0.0,
                             

In [8]:
y_pred = regressor_random.predict(X_test)
from sklearn.metrics import r2_score
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
print(r2_score(y_test, y_pred))
print(mean_absolute_error(y_test, y_pred))
mean_squared_error(y_test, y_pred)
print(np.sqrt(mean_squared_error(y_test, y_pred)))

0.1178208453493621
430.92943712500073
590.0344504636818


In [9]:
regressor_random.best_params_

{'learning_rate': 0.01,
 'max_depth': 1,
 'max_features': 'auto',
 'min_samples_leaf': 0.5,
 'min_samples_split': 0.5,
 'n_estimators': 150}

## GridSearchCV

In [10]:
from sklearn.model_selection import GridSearchCV

param_grid = {'n_estimators': [600, 800, 1000, 1200],
               'max_features': [1,2],
               'max_depth': [0.5, 1, 3, 4, 5, 7],
               'min_samples_split': [1, 2, 3, 6, 10],
               'min_samples_leaf': [1, 2, 5, 10, 20, 30],
               'learning_rate': [0.01, 0.02, 0.05, 0.1]}

regressor = GradientBoostingRegressor(random_state=42)

grid_search = GridSearchCV(estimator=regressor, param_grid=param_grid, cv=2, verbose=2, return_train_score=True)

grid_search.fit(X_train, y_train)

grid_search.best_estimator_

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integer 1

  FitFailedWarning)
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integer 1

  FitFailedWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test par

Fitting 2 folds for each of 5760 candidates, totalling 11520 fits
[CV] learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=1, min_samples_split=1, n_estimators=600 
[CV]  learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=1, min_samples_split=1, n_estimators=600, total=   0.0s
[CV] learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=1, min_samples_split=1, n_estimators=600 
[CV]  learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=1, min_samples_split=1, n_estimators=600, total=   0.0s
[CV] learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=1, min_samples_split=1, n_estimators=800 
[CV]  learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=1, min_samples_split=1, n_estimators=800, total=   0.0s
[CV] learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=1, min_samples_split=1, n_estimators=800 
[CV]  learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=1, min_sam

/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integer 1

  FitFailedWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integer 1

  FitFailedWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integ

[CV]  learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=2, min_samples_split=2, n_estimators=600, total=   0.1s
[CV] learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=2, min_samples_split=2, n_estimators=800 
[CV]  learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=2, min_samples_split=2, n_estimators=800, total=   0.2s
[CV] learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=2, min_samples_split=2, n_estimators=800 
[CV]  learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=2, min_samples_split=2, n_estimators=800, total=   0.2s
[CV] learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=2, min_samples_split=2, n_estimators=1000 
[CV]  learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=2, min_samples_split=2, n_estimators=1000, total=   0.2s
[CV] learning_rate=0.01, max_depth=0.5, max_features=1, min_samples_leaf=2, min_samples_split=2, n_estimators=1000 
[CV]  learning_ra

/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integer 1

  FitFailedWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integer 1

  FitFailedWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integ

...

[CV]  learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=20, min_samples_split=2, n_estimators=600, total=   0.1s
[CV] learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=20, min_samples_split=2, n_estimators=800 
[CV]  learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=20, min_samples_split=2, n_estimators=800, total=   0.1s
[CV] learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=20, min_samples_split=2, n_estimators=800 
[CV]  learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=20, min_samples_split=2, n_estimators=800, total=   0.1s
[CV] learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=20, min_samples_split=2, n_estimators=1000 
[CV]  learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=20, min_samples_split=2, n_estimators=1000, total=   0.2s
[CV] learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=20, min_samples_split=2, n_estimators=1000 
[CV]  learning_rate=0.1, max_dept

/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integer 1

  FitFailedWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integer 1

  FitFailedWarning)
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: min_samples_split must be an integer greater than 1 or a float in (0.0, 1.0]; got the integ

[CV]  learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=30, min_samples_split=2, n_estimators=600, total=   0.1s
[CV] learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=30, min_samples_split=2, n_estimators=800 
[CV]  learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=30, min_samples_split=2, n_estimators=800, total=   0.1s
[CV] learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=30, min_samples_split=2, n_estimators=800 
[CV]  learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=30, min_samples_split=2, n_estimators=800, total=   0.2s
[CV] learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=30, min_samples_split=2, n_estimators=1000 
[CV]  learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=30, min_samples_split=2, n_estimators=1000, total=   0.2s
[CV] learning_rate=0.1, max_depth=7, max_features=2, min_samples_leaf=30, min_samples_split=2, n_estimators=1000 
[CV]  learning_rate=0.1, max_dept

[Parallel(n_jobs=1)]: Done 11520 out of 11520 | elapsed: 26.7min finished


GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                          init=None, learning_rate=0.01, loss='ls',
                          max_depth=0.5, max_features=1, max_leaf_nodes=None,
                          min_impurity_decrease=0.0, min_impurity_split=None,
                          min_samples_leaf=1, min_samples_split=2,
                          min_weight_fraction_leaf=0.0, n_estimators=600,
                          n_iter_no_change=None, presort='deprecated',
                          random_state=42, subsample=1.0, tol=0.0001,
                          validation_fraction=0.1, verbose=0, warm_start=False)

In [11]:
grid_search.best_params_

{'learning_rate': 0.01,
 'max_depth': 0.5,
 'max_features': 1,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'n_estimators': 600}

In [12]:
# Accuracy metrics
y_pred_grid = grid_search.predict(X_test)
from sklearn.metrics import r2_score
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
print(r2_score(y_test, y_pred_grid))
print(mean_absolute_error(y_test, y_pred_grid))
mean_squared_error(y_test, y_pred_grid)
print(np.sqrt(mean_squared_error(y_test, y_pred_grid)))

-0.4705593165608766
628.2015069999998
761.7987353480838
